In [2]:
import pandas as pd
from datetime import datetime, timezone, timedelta
import pytz

with open("data/output.csv", "rb") as f:
    data = pd.read_csv(f, delimiter="\t")

In [3]:
JST = pytz.timezone("Asia/Tokyo")
CST = pytz.timezone("America/Chicago")

def to_jst_timestamp(s: str, format_str="%Y-%m-%d %H:%M:%S"):
    if type(s) is not str: return None
    naive_dt = datetime.strptime(s, format_str)
    jst_dt = JST.localize(naive_dt)
    cst_dt = jst_dt.astimezone(CST)
    return cst_dt

times = data["Time Played"]
times_mapped = times.map(to_jst_timestamp)
days_played = times_mapped.groupby(times_mapped.dt.date).count()
print(days_played.sort_values(ascending=False).head(10))

Time Played
2024-03-04    30
2024-05-01    26
2024-04-13    26
2024-04-25    25
2024-04-14    24
2024-04-20    23
2024-04-18    20
2024-04-24    19
2024-03-05    17
2024-03-10    17
Name: Time Played, dtype: int64


In [22]:
records_by_level = data.loc[data["Lamp"] != "Fail"].groupby(data["Rating"])
num_clears_by_level = records_by_level["Score"].count().rename("Clears")
average_scores_by_level = records_by_level["Score"].mean().round().astype("int").rename("Average")
def max_info(group):
    max_idx = group["Score"].idxmax()
    return group.loc[max_idx]
max_score_by_level = records_by_level.apply(max_info)[["Score", "Lamp", "Song Name"]]
result = pd.merge(num_clears_by_level, average_scores_by_level, on="Rating")
result = pd.merge(result, max_score_by_level, on="Rating")
print(result)

        Clears  Average                               Song Name   Score   Lamp
Rating                                                                        
8            7   895073                       朧 (dj TAKA Remix)  996620    GFC
9           25   918551                                 Why not  999650    PFC
10          29   921425                                  隅田川夏恋歌  992160    GFC
11          40   896780                                       朧  992520    GFC
12          56   890122                          MY SUMMER LOVE  987030    GFC
13          70   840879                                Struggle  978430    GFC
14         121   799834                      FUNKY SUMMER BEACH  943140     FC
15          26   798904                             未来（ダ）FUTURE  898400  Clear
16          16   770314                      Sword of Vengeance  861210  Clear
17           1   662870  PRANA+REVOLUTIONARY ADDICT (U1 DJ Mix)  662870  Clear
